In [2]:
import gradio as gr
import tensorflow as tf
import numpy as np
from PIL import Image

/Users/loic/Library/Python/3.9/lib/python/site-packages/urllib3/__init__.py:35: NotOpenSSLWarning: urllib3 v2 only supports OpenSSL 1.1.1+, currently the 'ssl' module is compiled with 'LibreSSL 2.8.3'. See: https://github.com/urllib3/urllib3/issues/3020
  warnings.warn(
/Users/loic/Library/Python/3.9/lib/python/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [2]:
model_path = "dogs-vs-cats-model_transferlearning.keras"
model = tf.keras.models.load_model(model_path)

In [9]:
# Define the core prediction function
def predict_cat_dog(image):
    # Preprocess image
    print(type(image))
    image = Image.fromarray(image.astype('uint8'))  # Convert numpy array to PIL image
    image = image.resize((150, 150)) #resize the image to 28x28 and converts it to gray scale
    image = np.array(image)
    image = np.expand_dims(image, axis=0) # same as image[None, ...]
    
    # Predict
    prediction = model.predict(image)
    
    # Because the output layer was dense(0) without an activation function, we need to apply sigmoid to get the probability
    # we could also change the output layer to dense(1, activation='sigmoid')
    prediction = np.round(float(tf.sigmoid(prediction)[0]), 2)
    p_cat = (1 - prediction)
    p_dog = prediction
    return {'cat': p_cat, 'dog': p_dog}

In [3]:
tf.sigmoid(0.55)

<tf.Tensor: shape=(), dtype=float32, numpy=0.6341356>

In [10]:
# Create the Gradio interface
input_image = gr.Image()
iface = gr.Interface(
    fn=predict_cat_dog,
    inputs=input_image, 
    outputs=gr.Label(),
    examples=["images/cat1.jpeg", "images/cat2.jpeg", "images/cat3.jpeg", "images/cat4.jpeg", "images/dog1.jpeg", "images/dog2.jpeg", "images/dog3.jpeg"],   
    description="A simple mlp classification model for image classification using the mnist dataset.")
iface.launch()

Running on local URL:  http://127.0.0.1:7863

To create a public link, set `share=True` in `launch()`.


<class 'numpy.ndarray'>
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 32ms/step


Traceback (most recent call last):
  File "/Users/loic/Library/Python/3.9/lib/python/site-packages/gradio/queueing.py", line 527, in process_events
    response = await route_utils.call_process_api(
  File "/Users/loic/Library/Python/3.9/lib/python/site-packages/gradio/route_utils.py", line 261, in call_process_api
    output = await app.get_blocks().process_api(
  File "/Users/loic/Library/Python/3.9/lib/python/site-packages/gradio/blocks.py", line 1786, in process_api
    result = await self.call_function(
  File "/Users/loic/Library/Python/3.9/lib/python/site-packages/gradio/blocks.py", line 1338, in call_function
    prediction = await anyio.to_thread.run_sync(
  File "/Users/loic/Library/Python/3.9/lib/python/site-packages/anyio/to_thread.py", line 56, in run_sync
    return await get_async_backend().run_sync_in_worker_thread(
  File "/Users/loic/Library/Python/3.9/lib/python/site-packages/anyio/_backends/_asyncio.py", line 2144, in run_sync_in_worker_thread
    return await futur